In [3]:
import pandas

df = pandas.read_csv("../../exp202/ground_truth_16_expertsname.tsv", sep="\t").drop('Unnamed: 0', axis=1)

In [4]:
df.head(20)

nmvw_uri  \
0   https://hdl.handle.net/20.500.11840/pi57757   
1    https://hdl.handle.net/20.500.11840/pi3325   
2   https://hdl.handle.net/20.500.11840/pi76219   
3   https://hdl.handle.net/20.500.11840/pi76219   
4   https://hdl.handle.net/20.500.11840/pi77221   
5   https://hdl.handle.net/20.500.11840/pi63457   
6   https://hdl.handle.net/20.500.11840/pi56613   
7   https://hdl.handle.net/20.500.11840/pi46240   
8   https://hdl.handle.net/20.500.11840/pi81078   
9   https://hdl.handle.net/20.500.11840/pi64129   
10  https://hdl.handle.net/20.500.11840/pi21230   
11  https://hdl.handle.net/20.500.11840/pi69372   
12   https://hdl.handle.net/20.500.11840/pi1095   
13  https://hdl.handle.net/20.500.11840/pi82759   
14  https://hdl.handle.net/20.500.11840/pi42477   
15  https://hdl.handle.net/20.500.11840/pi40216   

                                           pref_label birth_begin_time  \
0                     J.J. (Johan Jacob) KorndÃ¶rffer             1829   
1                F.W. (Friedrich Wilhelm) Stammeshaus             1881   
2                               L. (Louis) van Vuuren             1873   
3                               L. (Louis) van Vuuren             1873   
4                            Jean Louis Henry Beijens             1835   
5                                 S.J. (Sjoerd) Nauta              NaN   
6   W.G.A.C. (Willem Gerardus Antonius Cornelis) C...       1854-04-28   
7                   J.C. (Johannes Cornelis) Wienecke             1872   
8                        S. (Sophia) Swaan-Hannivoort             1901   
9                                  Adolphe Zimmermans       1858-04-02   
10        G.C.E. (Gotfried Coenraad Ernst) van Daalen             1863   
11               G.F.B. (George Felix Bernard) Watrin       1869-11-08   
12                         H.T. (Henri Titus) DamstÃ©             1874   
13                 Baron Haro van Hemert tot Dingshof             1879   
14                          J.C. (Jean Charles) Pabst       1873-03-08   
15                              T. (Theodorus) Poland             1796   

   birth_end_time death_begin_time death_end_time  ConstituentID  \
0            1829             1882           1882         7329.0   
1            1881             1957           1957        10400.0   
2            1873             1951           1951         7323.0   
3            1873             1951           1951         1381.0   
4            1835             1914           1914         9805.0   
5             NaN              NaN            NaN         1447.0   
6      1854-04-28       1915-07-12     1915-07-12         1150.0   
7            1872             1945           1945         3583.0   
8            1901       1990-09-21     1990-09-21        14942.0   
9      1858-04-02       1922-07-02     1922-07-02         5995.0   
10           1863             1930           1930         1125.0   
11     1869-11-08       1935-08-02     1935-08-02         1533.0   
12           1874             1955           1955         9678.0   
13           1879             1972           1972         1350.0   
14     1873-03-08       1942-01-24     1942-01-24        12116.0   
15           1796             1857           1857          330.0   

                                            AlphaSort  \
0   Korndörffer J.J. RMWO-4 + EV 1e Luitenant Infa...   
1                       Stammeshaus Friedrich Wilhelm   
2   Vuuren L. van OON, EV 1e Luitenant der Infante...   
3                             Vuuren L. van Professor   
4                            Beijens Jean Louis Henri   
5       Rijksmuseum Justinus van Nassau, Nauta Sjoerd   
6        Christan W.G.A.C. RMWO-3, ES Generaal-majoor   
7                                       Wienecke J.C.   
8                                Swaan-Hannivoort, S.   
9                                  Zimmermans Adolphe   
10               Daalen G.C.E. van Luitenant-generaal   
11             Watrin G.A. reserve-Kapitein KNIL b.d.   
12            

### Filter triples linked with these 16 URIs

In [ ]:
import rdflib

def filter_constituent_query(uri, file, new_graph):
    g = rdflib.Graph().parse(file)
    
    if len(g) == 0:
        print(f"{file}: The graph len is zero")
        return

    q = f"""
    PREFIX crm: <http://www.cidoc-crm.org/cidoc-crm/>
    PREFIX la: <https://linked.art/ns/terms/>
    PREFIX wd: <http://www.wikidata.org/entity/>
    PREFIX wdt: <http://www.wikidata.org/prop/direct/>


    CONSTRUCT {{
       <{uri}> ?prop ?val .
       ?child ?childProp ?childPropVal . 
       ?someSubj ?incomingChildProp ?child .
    }}
    WHERE {{
        <{uri}> a crm:E21_Person.
         <{uri}> ?prop ?val ;
             (a|!a)+ ?child . 
         ?child ?childProp ?childPropVal.
         ?someSubj ?incomingChildProp ?child. 
         FILTER(?child != <http://vocab.getty.edu/aat/300404670>).
    }}
    """

    for row in g.query(q):
        new_graph.add(row)

    return new_graph

In [ ]:
import rdflib

def test_filter_constituent_query():
    assert len(filter_constituent_query(rdflib.URIRef(str("https://hdl.handle.net/20.500.11840/pi25284")), "/Users/sarah_shoilee/PycharmProjects/entity_linking/nmvw_data/ccrdfconst/ccrdfconst_1-20.ttl", rdflib.Graph())) == 40, "Should be 40"
    
test_run_query()

In [ ]:
import os, time

def run(directory):
    new_graph = rdflib.Graph()
    
    try:
        for subdir, dirs, files in os.walk(directory):
            files = [f for f in files if f.endswith(".ttl")]
            for file in sorted(files, key=lambda s: int(s.split("-")[-1].split(".")[-2])):
                if file is None:
                    continue
                
                start_time = time.time()
                for _ , row in df.iterrows():
                    uri = row['nmvw_uri']
                    new_graph = new_graph + filter_constituent_query(uri, os.path.join(directory, file), new_graph)
                    
                print(f"file: {file.split('/')[-1]}, runtime: {round((time.time() - start_time), 4)}")

    finally:
        # store the newly constructed graph in one file
        new_graph.serialize(destination=os.path.join(os.getcwd(), "constituents_15.ttl"))
        

In [ ]:
run("../nmvw_data/ccrdfconst")

### Filter object triples which has these 20 actors

In [4]:
import rdflib

# Load data in a graph and run the query and add them to the new graph
def filter_object_by_constituent_query(uri, file, new_graph):
    g = rdflib.Graph().parse(file)

    if len(g) == 0:
        return

    q = f"""
    PREFIX crm: <http://www.cidoc-crm.org/cidoc-crm/>
    PREFIX la: <https://linked.art/ns/terms/>
    PREFIX wd: <http://www.wikidata.org/entity/>
    PREFIX wdt: <http://www.wikidata.org/prop/direct/>


    CONSTRUCT {{
       ?object a crm:E22_Human-Made_Object .
       ?object ?prop ?val .
       ?child ?childProp ?childPropVal . 
       ?someSubj ?incomingChildProp ?child .
    }}
    WHERE {{
        ?event ?prop <{uri}>. 
         ?event crm:P24_transferred_title_of ?object .
         ?object a crm:E22_Human-Made_Object ;
             (a|!a)+ ?child . 
         ?child ?childProp ?childPropVal.
         ?someSubj ?incomingChildProp ?child. 
         # FILTER(?child != <http://vocab.getty.edu/aat/300404670>).
    }}
    """
    
    if len(g.query(q)) > 0:
        print(len(g.query(q)))

    for row in g.query(q):
        new_graph.add(row)

    return new_graph

In [5]:
import os, time
from tqdm import tqdm

def filter_object_by_constituent(directory):
    print()
    new_graph = rdflib.Graph()
    
    try:
        for subdir, dirs, files in os.walk(directory):
            files = [f for f in files if f.endswith(".ttl")]
            for file in tqdm(files):
                if file is None:
                    continue
                
                start_time = time.time()
                for _ , row in df.iterrows():
                    uri = row['nmvw_uri']
                    new_graph = new_graph + filter_object_by_constituent_query(uri, os.path.join(directory, file), new_graph)
                    
                print(f"file: {file.split('/')[-1]}, runtime: {round((time.time() - start_time), 4)}")
    finally:
        # store the newly constructed graph in one file
        new_graph.serialize(destination=os.path.join(os.getcwd(), "objects_from_15_const.ttl"))

TODO: run the next piece of code;

In [7]:
filter_object_by_constituent("/Users/sarah_shoilee/PycharmProjects/entity_linking/nmvw_data/ccrdfobjacquisition")

  0%|                                       | 1/4872 [00:21<29:12:07, 21.58s/it]

file: ccrdfobjacquisition_194301-194400.ttl, runtime: 21.5822



  0%|                                       | 2/4872 [00:40<26:45:09, 19.78s/it]

file: ccrdfobjacquisition_92801-92900.ttl, runtime: 18.511



  0%|                                       | 3/4872 [00:53<22:55:27, 16.95s/it]

...

file: ccrdfobjacquisition_105201-105300.ttl, runtime: 27.2853



  6%|█▉                                 | 277/4872 [5:20:08<39:41:43, 31.10s/it]

file: ccrdfobjacquisition_174001-174100.ttl, runtime: 30.9793


  6%|█▉                                 | 277/4872 [5:20:16<88:32:50, 69.37s/it]


KeyboardInterrupt: 

TODO: convert bronbeek data to RDF

TODO: convert to csv format both data set

TODO: do the linking based on initials+surname

### Insert owl:sameAs property on the corresponding URIs found on the resultant csv from the privous step

In [5]:
import rdflib, os
from rdflib import Graph, URIRef
from rdflib.namespace import OWL

def create_link_graph(df):
    g = Graph()

    for _ , row in df.iterrows():
        uri_nmvw = str(row['nmvw_uri'])
        constituent_id_bronbeek = str(row['ConstituentID'])
        uri_bronbeek = "https://example.com/Constituents/" + constituent_id_bronbeek

        uri_nmvw = URIRef(uri_nmvw)
        uri_bronbeek = URIRef(uri_bronbeek)

        g.add((uri_nmvw, OWL.sameAs, uri_bronbeek))
    
    return g

create_link_graph(df).serialize(destination=os.path.join(os.getcwd(), 'constituents_links.ttl'))

<Graph identifier=Nc05d2b4a6c7c4ad9a36081873169f8ba (<class 'rdflib.graph.Graph'>)>

Why I am doing all these? In order to do, what? 